In [11]:
import sys
sys.path.append("../src") 
from dolfin import *
import meshio
import pyvista as pv
import numpy as np
from utils import *
from materials import *
import fea_transient
import LB_transient
import max_omega 

In [12]:
mesh_file = "../mesh/disk.inp" # .inp or .xdmf
comp_list = np.linspace(1.,1.,1) # a list defining the composition, e.g., [1,0.9,0.5,0.4,0.3]

mesh = read_mesh(mesh_file)
properties = get_properties(mesh,comp_list)
Displacement_BC = 'fix-free' # fix-free or free-free

t_rise = 1. # time to heat to the max temp.
t_heatdwell = 20. # heating dwell time
t_fall = 3. # time to cool to the ambient temp
t_cooldwell = 600. # cooling dwell time

In [3]:
def run_fea_wrap(omega,T_load):
    n_cyc = 15 # number of simulated cycles

    time_step = 1. # time step size
    time_step_coarse = 20. # use a coarser time step at during cooling dwell
    plastic_inverval = 1 # elasto-plastic simulation every N thermal time step
    
    load = get_loadfunc(T_load,t_rise,t_heatdwell,t_fall,t_cooldwell)

    t_cycle = t_rise + t_heatdwell + t_fall + t_cooldwell
    t_fine = t_rise + t_heatdwell + t_fall*2.
    t_list = get_time_list(t_cycle,t_fine,time_step,time_step_coarse,n_cyc)
    
    results = fea_transient.run_simulation(mesh,properties,load,omega,t_list,Displacement_BC,plastic_inverval)
    PEEQ = results[:,1]
    period = (len(PEEQ)-1)/n_cyc
    assert period-int(period) == 0
    SD_flag = fea_transient.check_PEEQ(PEEQ,int(period),tol=1e-8)
    return SD_flag

In [13]:
def run_lb_wrap(omega,T_load):
    time_step = 1. # time step size
    time_step_coarse = 10. # use a coarser time step at during cooling dwell
    plastic_inverval = 1 # elasto-plastic simulation every N thermal time step
    
    sd_flag = LB_transient.run(mesh,properties,T_load,omega,t_rise,t_heatdwell,t_fall,t_cooldwell,
                 Displacement_BC,time_step,time_step_coarse)
    
    if sd_flag.max()>1.001:
        print('Not Shakedown!')
        SD_flag = 0
    else:
        print('Shakedown!')
        SD_flag = 1
    return SD_flag

In [5]:
%%time
run_fea_wrap(1000,1000)

/home/bizon/anaconda3/envs/fenicsproject/lib/python3.11/site-packages/ffc/jitcompiler.py:234: QuadratureRepresentationDeprecationWarning: 
*** ===================================================== ***
*** FFC: quadrature representation is deprecated! It will ***
*** likely be removed in 2018.2.0 release. Use uflacs     ***
*** representation instead.                               ***
*** ===================================================== ***
  issue_deprecation_warning()


Solving linear variational problem.
Residual0: 1024459.2213370615
Residual: 74696.62859724437
Residual: 155.31270838853357
Residual: 0.02700703539685462
Solving linear variational problem.
Residual0: 416476.3087531488
Residual: 21814.74422397166
Residual: 134.4970938643543
Residual: 0.013096902327918509
Solving linear variational problem.
Residual0: 299719.57958379004
Residual: 5685.623568781592
Residual: 17.17181960175918
Residual: 0.00026619718135377317
Solving linear variational problem.
Residual0: 236663.37061989243
Residual: 5274.437305891782
Residual: 17.933136432070757
Residual: 0.0005595955316493898
Solving linear variational problem.
Residual0: 196919.27321156472
Residual: 5365.860852804877
Residual: 13.312397088867387
Residual: 0.00016337736406840016
Solving linear variational problem.
Residual0: 169518.89232715126
Residual: 3966.656107565352
Residual: 9.213739684261215
Residual: 0.00016839249938583383
Solving linear variational problem.
Residual0: 149426.5252691222
Residual:

Residual: 0.1052904682489508
Solving linear variational problem.
Residual0: 90468.86841857914
Residual: 21.170746944438555
Residual: 8.909886869213856e-05
Solving linear variational problem.
Residual0: 85234.11568849723
Residual: 1.5286989589852482
Residual: 1.4000172976709718e-06
Solving linear variational problem.
Residual0: 80637.87189213771
Residual: 18.535927639412716
Residual: 7.167141767577465e-05
Solving linear variational problem.
Residual0: 76566.19069174382
Residual: 0.922958164956804
Residual: 4.6279213340245334e-07
Solving linear variational problem.
Residual0: 72931.10140265075
Residual: 65.13079621397485
Residual: 0.00144876668353071
Solving linear variational problem.
Residual0: 69663.54982258748
Residual: 2.800621882032956
Residual: 5.249747357127053e-06
Solving linear variational problem.
Residual0: 66708.53491400692
Residual: 0.6969514187669338
Residual: 1.2691953826800627e-07
Solving linear variational problem.
Residual0: 64021.677863612524
Residual: 14.350646603868

Residual: 0.0003058798967033927
Solving linear variational problem.
Residual0: 936677.349358028
Residual: 14004.681355887233
Residual: 67.81458001625029
Residual: 0.0033467992589766293
Solving linear variational problem.
Residual0: 382943.06146905874
Residual: 732.8191162051029
Residual: 0.1793229344005274
Solving linear variational problem.
Residual0: 200815.77858511737
Residual: 264.4142605506908
Residual: 4.970581712573032
Residual: 7.788913998955716e-06
Solving linear variational problem.
Residual0: 122671.04152542721
Residual: 223.9932931450415
Residual: 0.00080513709899477
Solving linear variational problem.
Residual0: 82765.49490988684
Residual: 97.79228780617737
Residual: 0.00019411217542012523
Solving linear variational problem.
Residual0: 59809.57101628468
Residual: 31.31829659125162
Residual: 0.00010115706919204547
Solving linear variational problem.
Residual0: 45427.080691685325
Residual: 46.88890711042854
Residual: 2.333422835187127e-10
Solving linear variational problem.


Residual: 2.7145895334183e-10
Solving linear variational problem.
Residual0: 7793.287258289829
Residual: 2.081608965274782e-10
Solving linear variational problem.
Residual0: 7254.966739450377
Residual: 2.3460999388491965e-10
Solving linear variational problem.
Residual0: 6783.426248093681
Residual: 2.3209736797031327e-10
Solving linear variational problem.
Residual0: 6366.627580180768
Residual: 1.9436777712626046e-10
Solving linear variational problem.
Residual0: 5995.01857364448
Residual: 1.9966842302676267e-10
Solving linear variational problem.
Residual0: 5660.989391271003
Residual: 1.9321634217900868e-10
Solving linear variational problem.
Residual0: 5358.454783462298
Residual: 2.1523929659523917e-10
Solving linear variational problem.
Residual0: 5082.530009906555
Residual: 2.0463199093789566e-10
Solving linear variational problem.
Residual0: 4829.277875218534
Residual: 1.792603865578732e-10
Solving linear variational problem.
Residual0: 4595.5105558847945
Residual: 1.8569258933456

...

Residual: 10.967330856276654
Residual: 0.0001086888066379313
Solving linear variational problem.
Residual0: 111785.88588482418
Residual: 51.89928732142504
Residual: 0.00034238895839800186
Solving linear variational problem.
Residual0: 103496.91788606957
Residual: 19.090846909715726
Residual: 7.211120659274321e-05
Solving linear variational problem.
Residual0: 96480.73274223391
Residual: 1090.0410931939357
Residual: 0.5604929583442534
Solving linear variational problem.
Residual0: 90456.46329010343
Residual: 21.16670549836337
Residual: 7.258203048904262e-05
Solving linear variational problem.
Residual0: 85221.02064576537
Residual: 1.8355585638165461
Residual: 1.9396456543931167e-06
Solving linear variational problem.
Residual0: 80624.15480400989
Residual: 18.74369685519725
Residual: 7.066890558439286e-05
Solving linear variational problem.
Residual0: 76551.87239202463
Residual: 1.0978983252607275
Residual: 6.232026817482359e-07
Solving linear variational problem.
Residual0: 72916.201333

Solving linear variational problem.
Residual0: 500217.2228845247
Residual: 29080.899401426566
Residual: 129.08936778031918
Residual: 0.030035139232583257
Solving linear variational problem.
Residual0: 291854.9520462831
Residual: 9175.34549970931
Residual: 81.79099019193151
Residual: 0.008079944897393674
Solving linear variational problem.
Residual0: 219290.03231141003
Residual: 3907.8407955465364
Residual: 15.90268528045039
Residual: 0.0004650832074747302
Solving linear variational problem.
Residual0: 174753.45265053966
Residual: 3263.8192040990107
Residual: 10.944225300559633
Residual: 0.00028906248752429684
Solving linear variational problem.
Residual0: 936692.401791459
Residual: 13863.498962756792
Residual: 41.24563762230704
Residual: 0.0012786176109112594
Solving linear variational problem.
Residual0: 382971.9029705921
Residual: 6545.286976232313
Residual: 13.362837111230668
Residual: 0.00011579293848125662
Solving linear variational problem.
Residual0: 200860.44450418928
Residual:

Residual: 0.00012644318553822108
Solving linear variational problem.
Residual0: 45529.22806149124
Residual: 49.494246023561054
Residual: 2.2196621426419496e-10
Solving linear variational problem.
Residual0: 35934.774503572204
Residual: 6.324192187548336e-10
Solving linear variational problem.
Residual0: 29205.134383513807
Residual: 5.776294486571529e-10
Solving linear variational problem.
Residual0: 24297.016959254495
Residual: 4.5412689006816244e-10
Solving linear variational problem.
Residual0: 20603.412180865656
Residual: 3.745791929276493e-10
Solving linear variational problem.
Residual0: 17752.25652100625
Residual: 3.701281848099716e-10
Solving linear variational problem.
Residual0: 15505.163435063274
Residual: 3.537123937538304e-10
Solving linear variational problem.
Residual0: 13703.333925601024
Residual: 3.176177909092732e-10
Solving linear variational problem.
Residual0: 12237.251409830145
Residual: 3.0347252528913216e-10
Solving linear variational problem.
Residual0: 11029.03

Residual: 2.0267511919414262e-10
Solving linear variational problem.
Residual0: 5691.840877127135
Residual: 2.0238732676352124e-10
Solving linear variational problem.
Residual0: 5388.2211858948585
Residual: 2.11970496971363e-10
Solving linear variational problem.
Residual0: 5111.22162517896
Residual: 2.0996094605370034e-10
Solving linear variational problem.
Residual0: 4856.911860477813
Residual: 2.1494906240136182e-10
Solving linear variational problem.
Residual0: 4622.109178753094
Residual: 1.916245872536672e-10
Solving linear variational problem.
Residual0: 4404.223242463331
Residual: 1.941600103903448e-10
Solving linear variational problem.
Residual0: 1024495.9470299683
Residual: 48697.585057810335
Residual: 204.62875367210938
Residual: 0.06988259016927988
Solving linear variational problem.
Residual0: 416463.6295662673
Residual: 12173.635511994533
Residual: 88.84544250237107
Residual: 0.007949590445224317
Solving linear variational problem.
Residual0: 299701.4154367063
Residual: 2

0

In [6]:
%%time
run_lb_wrap(1000,1000)

Simulation time: 1.0
Solving linear variational problem.
    Residual0: 1024459.2213370615
    Residual: 74696.62859724436
    Residual: 155.31270838826262
    Residual: 0.027007035314247755
Simulation time: 2.0
Solving linear variational problem.
    Residual0: 416476.3087531487
    Residual: 21814.74422397124
    Residual: 134.49709386455044
    Residual: 0.013096902611780821
Simulation time: 3.0
Solving linear variational problem.
    Residual0: 299719.57958379004
    Residual: 5685.623568781833
    Residual: 17.17181960175667
    Residual: 0.00026619719613023464
Simulation time: 4.0
Solving linear variational problem.
    Residual0: 236663.37061989243
    Residual: 5274.437305891691
    Residual: 17.93313643205313
    Residual: 0.0005595955814035642
Simulation time: 5.0
    Residual0: 196919.27321156472
Solving linear variational problem.
    Residual: 5365.8608528053965
    Residual: 13.312397088814821
    Residual: 0.00016337729440919259
Simulation time: 6.0
Solving linear variat

    Residual: 1.374705396606124e-10
Simulation time: 327.0
Solving linear variational problem.
    Residual0: 4848.7942632409095
    Residual: 1.2585545491006162e-10
Simulation time: 337.0
Solving linear variational problem.
    Residual0: 4568.710195417502
    Residual: 1.2558364563722453e-10
Simulation time: 347.0
Solving linear variational problem.
    Residual0: 4314.509112437574
    Residual: 1.1683825322445608e-10
Simulation time: 357.0
Solving linear variational problem.
    Residual0: 4083.3120183051665
    Residual: 1.0923983830544363e-10
Simulation time: 367.0
Solving linear variational problem.
    Residual0: 3872.603474716012
    Residual: 1.3193661492572254e-10
Simulation time: 377.0
Solving linear variational problem.
    Residual0: 3680.176019679823
    Residual: 9.741352486057998e-11
Simulation time: 387.0
Solving linear variational problem.
    Residual0: 3504.0852015122214
    Residual: 1.1381913018683213e-10
Simulation time: 397.0
Solving linear variational problem.


0

In [7]:
omega_max = max_omega.run(mesh,properties,Displacement_BC)

Trying Omega =  1000
Residual =  712.9074408028031
Residual =  3.4055434212194736e-09
Trying Omega =  2000
Residual =  2138.7223224080353
Residual =  1.0983953119697916e-08
Trying Omega =  3000
Residual =  3564.5372040135585
Residual =  45.87963485350336
Residual =  5.011880238031026
Residual =  0.0018096691405953317
Trying Omega =  4000
Residual =  4990.352085608339
Residual =  57714.216999863485
Residual =  49935.864952500124
Residual =  30374.5499025083
Residual =  28686.44689192395
Residual =  28882.46298761872
Residual =  2055.3293543949526
Residual =  97.0677985278105
Residual =  0.11420573443387562
Residual =  5.706316802851251e-07
Trying Omega =  3500.0
Residual =  2316.949182598206
Residual =  2065.433230909465
Residual =  275.11437047453734
Residual =  22.80595803782277
Residual =  0.1668587715624196
Residual =  1.1949828552811801e-05
Trying Omega =  4000.0
Residual =  2673.402903011
Residual =  65390.0839090167
Residual =  46874.14428805548
Residual =  27349.800485167325
Res

In [8]:
num_om = 5
omega_list = (np.arange(1,num_om)/num_om*omega_max**2)**0.5
omega_list

array([1779.24627741, 2516.23421631, 3081.74495165, 3558.49255482])

In [9]:
T_tol = 10
T_SD_list_fea = []
for omega in omega_list:
    T_min = 0.
    T_max = 2000.
    while (T_max-T_min)>T_tol:
        T_load = (T_max+T_min)/2.
        flag = run_fea_wrap(omega,T_load)
        if flag == 1:
            T_min = T_load
        else:
            T_max = T_load
    T_SD_list_fea.append((T_max+T_min)/2.)
T_SD_list_fea

Solving linear variational problem.
Residual0: 1024372.0045245815
Residual: 71301.4798697885
Residual: 153.7813818522258
Residual: 0.03151748249830429
Solving linear variational problem.
Residual0: 416476.3104181772
Residual: 18155.719945239925
Residual: 118.63938807032648
Residual: 0.012138717054580637
Solving linear variational problem.
Residual0: 299719.57883683586
Residual: 10965.221900002416
Residual: 64.40856506368573
Residual: 0.006705896141571646
Solving linear variational problem.
Residual0: 236663.37053694428
Residual: 2630.467292314082
Residual: 6.356687676832471
Residual: 7.31964459760862e-05
Solving linear variational problem.
Residual0: 196919.27324993466
Residual: 1966.3845024265217
Residual: 2.0495827262014
Residual: 3.987511310670971e-06
Solving linear variational problem.
Residual0: 169518.89228429552
Residual: 1285.210857052611
Residual: 1.3626025460898232
Solving linear variational problem.
Residual0: 149426.36948800387
Residual: 67.58832890477618
Residual: 0.002871

Residual: 0.9244940375270759
Residual: 5.142411883516601e-07
Solving linear variational problem.
Residual0: 72931.10140264432
Residual: 40.41125997774164
Residual: 0.0005788381070703202
Solving linear variational problem.
Residual0: 69663.54987357502
Residual: 3.102414370953979
Residual: 6.468742920380587e-06
Solving linear variational problem.
Residual0: 66708.53491404143
Residual: 0.7021321717155581
Residual: 1.1873226254683174e-07
Solving linear variational problem.
Residual0: 64021.67786361049
Residual: 14.305938904427451
Residual: 5.538230470557217e-05
Solving linear variational problem.
Residual0: 61566.75544544527
Residual: 0.48954092818927547
Solving linear variational problem.
Residual0: 339018.5074308248
Residual: 19775.214171491698
Residual: 4.2290837175252814e-10
Solving linear variational problem.
Residual0: 431078.0500475057
Residual: 13833.257027838554
Residual: 104.46046942329436
Residual: 0.024617510149390252
Solving linear variational problem.
Residual0: 500217.108150

Residual0: 200815.77974535
Residual: 263.3529548698628
Residual: 0.006553697524382655
Solving linear variational problem.
Residual0: 122671.0416421458
Residual: 223.68374415904267
Residual: 0.0008223134924765805
Solving linear variational problem.
Residual0: 82765.49491168742
Residual: 98.27827067866396
Residual: 1.0967993244472132
Residual: 4.111350817690015e-07
Solving linear variational problem.
Residual0: 59809.57100901586
Residual: 122.80433688228385
Residual: 6.37845977189004e-05
Solving linear variational problem.
Residual0: 45427.08069831557
Residual: 46.54179935184122
Residual: 2.0478219807149173e-10
Solving linear variational problem.
Residual0: 35822.49108414109
Residual: 6.777919467551979e-10
Solving linear variational problem.
Residual0: 29084.599099788025
Residual: 5.435592045711246e-10
Solving linear variational problem.
Residual0: 24169.991186721865
Residual: 4.5429827141745455e-10
Solving linear variational problem.
Residual0: 20471.497393628055
Residual: 4.02576423039

Residual: 2.9666174158249653e-10
Solving linear variational problem.
Residual0: 9135.4077133012
Residual: 2.51116357150382e-10
Solving linear variational problem.
Residual0: 8413.629961835488
Residual: 2.3262905717610814e-10
Solving linear variational problem.
Residual0: 7793.287258289849
Residual: 2.1635616393406104e-10
Solving linear variational problem.
Residual0: 7254.966739450382
Residual: 2.0755393967524343e-10
Solving linear variational problem.
Residual0: 6783.426248093674
Residual: 2.1033359412715385e-10
Solving linear variational problem.
Residual0: 6366.627580180776
Residual: 2.0082666922517035e-10
Solving linear variational problem.
Residual0: 5995.018573644472
Residual: 2.0566291601554755e-10
Solving linear variational problem.
Residual0: 5660.9893912709995
Residual: 1.917665182161204e-10
Solving linear variational problem.
Residual0: 5358.4547834622845
Residual: 2.1407050096478138e-10
Solving linear variational problem.
Residual0: 5082.530009906552
Residual: 1.95917381561

Residual: 7.686336577245106e-05
Solving linear variational problem.
Residual0: 236640.37280115357
Residual: 2532.3333537218195
Residual: 7.102867707374138
Residual: 0.0001253905204758075
Solving linear variational problem.
Residual0: 196891.83733442213
Residual: 148.85314249334877
Residual: 0.007258275964648136
Solving linear variational problem.
Residual0: 169487.35116983886
Residual: 3059.3206913836516
Residual: 5.621453937657827
Residual: 3.4745899988178655e-05
Solving linear variational problem.
Residual0: 149391.15325004046
Residual: 62.151178134510396
Residual: 0.0006536984806871078
Solving linear variational problem.
Residual0: 133977.824844665
Residual: 1509.1993323950417
Residual: 1.3440377181415653
Residual: 3.9699137726798925e-06
Solving linear variational problem.
Residual0: 121748.52864088427
Residual: 10.532730140487466
Residual: 9.877406280981078e-05
Solving linear variational problem.
Residual0: 111785.94917947047
Residual: 52.61237714223712
Residual: 0.0003401227175776

...

Residual: 1.5058729524718322e-10
Solving linear variational problem.
Residual0: 5704.1246834297535
Residual: 1.3751126148908033e-10
Solving linear variational problem.
Residual0: 4745.507831361181
Residual: 1.345769405814399e-10
Solving linear variational problem.
Residual0: 4024.1005221991304
Residual: 1.3432967142291091e-10
Solving linear variational problem.
Residual0: 3467.2340938599514
Residual: 1.2823954038729104e-10
Solving linear variational problem.
Residual0: 3028.3486701248994
Residual: 1.1660459664991517e-10
Solving linear variational problem.
Residual0: 2676.4288178903475
Residual: 1.1486950036944102e-10
Solving linear variational problem.
Residual0: 2390.084575955656
Residual: 1.0585422174483985e-10
Solving linear variational problem.
Residual0: 2154.1038758928253
Residual: 9.613239998249397e-11
Solving linear variational problem.
Residual0: 1957.3768128463116
Residual: 9.578857359909372e-11
Solving linear variational problem.
Residual0: 1791.6072194911717
Residual: 9.378

Residual0: 21833.18081944882
Residual: 2.5452548181549655e-10
Solving linear variational problem.
Residual0: 20214.24175730525
Residual: 2.1756140661348832e-10
Solving linear variational problem.
Residual0: 18843.893096131174
Residual: 2.437711557704963e-10
Solving linear variational problem.
Residual0: 17667.267941811402
Residual: 2.1301225840324408e-10
Solving linear variational problem.
Residual0: 16644.730575313653
Residual: 2.358642054395987e-10
Solving linear variational problem.
Residual0: 15746.905214857781
Residual: 1.9813769049459005e-10
Solving linear variational problem.
Residual0: 14951.537555480585
Residual: 2.4094913788346585e-10
Solving linear variational problem.
Residual0: 14241.44555081699
Residual: 2.0255240373687277e-10
Solving linear variational problem.
Residual0: 13603.141830509468
Residual: 1.9702815770612098e-10
Residual0: 13025.883740229645
Solving linear variational problem.
Residual: 1.9260498231545541e-10
Solving linear variational problem.
Residual0: 1250

Residual: 1.0178443590665246e-10
Solving linear variational problem.
Residual0: 1791.610690789106
Residual: 9.454609255022536e-11
Solving linear variational problem.
Residual0: 1650.4918257724155
Residual: 9.585713133831903e-11
Solving linear variational problem.
Residual0: 1529.1625850278967
Residual: 9.72857975844147e-11
Solving linear variational problem.
Residual0: 1423.8365886423535
Residual: 1.0507059895327682e-10
Solving linear variational problem.
Residual0: 1331.541465426827
Residual: 9.191386536631289e-11
Solving linear variational problem.
Residual0: 1249.929995341414
Residual: 9.604580067291008e-11
Solving linear variational problem.
Residual0: 1177.1398897523081
Residual: 9.135469703637917e-11
Solving linear variational problem.
Residual0: 1111.687625321796
Residual: 8.677659773585512e-11
Solving linear variational problem.
Residual0: 1052.3869059966862
Residual: 9.49541416246688e-11
Solving linear variational problem.
Residual0: 998.2854308976844
Residual: 9.0782532181771

Solving linear variational problem.
Residual0: 13025.88373119471
Residual: 2.344453067273541e-10
Solving linear variational problem.
Residual0: 12501.00339865874
Residual: 2.1288124563372577e-10
Solving linear variational problem.
Residual0: 12021.425789471905
Residual: 0.008804938291797843
Solving linear variational problem.
Residual0: 66214.15939435716
Residual: 243.65226685449642
Residual: 1.1710636002397313e-10
Solving linear variational problem.
Residual0: 84194.7778031683
Residual: 4.1635401965438335e-10
Solving linear variational problem.
Residual0: 97698.67486967285
Residual: 5.377703722540116e-10
Solving linear variational problem.
Residual0: 57002.92004533548
Residual: 2.91421750652217e-10
Solving linear variational problem.
Residual0: 42830.084426740184
Residual: 2.275665214392122e-10
Solving linear variational problem.
Residual0: 34131.533720870575
Residual: 2.3066671666739406e-10
Solving linear variational problem.
Residual0: 182947.73475685742
Residual: 1.4087107392927043

[589.84375, 589.84375, 66.40625, 191.40625]

In [14]:
%%time
T_tol = 10
T_SD_list_sd = []
for omega in omega_list:
    T_min = 0.
    T_max = 2000.
    while (T_max-T_min)>T_tol:
        T_load = (T_max+T_min)/2.
        flag = run_lb_wrap(omega,T_load)
        if flag == 1:
            T_min = T_load
        else:
            T_max = T_load
    T_SD_list_sd.append((T_max+T_min)/2.)
T_SD_list_sd

Simulation time: 1.0
Solving linear variational problem.
    Residual0: 1024372.0045245815
    Residual: 71301.47986978845
    Residual: 153.78138185266883
    Residual: 0.0315174819414255
Simulation time: 2.0
Solving linear variational problem.
    Residual0: 416476.31041817745
    Residual: 18155.719945240497
    Residual: 118.63938807035532
    Residual: 0.012138716985826479
Simulation time: 3.0
Solving linear variational problem.
    Residual0: 299719.5788368358
    Residual: 10965.22190000185
    Residual: 64.40856506368159
    Residual: 0.00670589614626298
Simulation time: 4.0
Solving linear variational problem.
    Residual0: 236663.37053694428
    Residual: 2630.467292313746
    Residual: 6.356687676857025
    Residual: 7.319650627007235e-05
Simulation time: 5.0
Solving linear variational problem.
    Residual0: 196919.27324993466
    Residual: 1966.3845024264238
    Residual: 2.0495827261745507
    Residual: 3.987514415882793e-06
Simulation time: 6.0
Solving linear variational

    Residual: 1.6680188931211024e-10
Simulation time: 297.0
Solving linear variational problem.
    Residual0: 5880.1719900800545
    Residual: 1.4634689674144022e-10
Simulation time: 307.0
Solving linear variational problem.
    Residual0: 5500.378509680127
    Residual: 1.3641675576363833e-10
Simulation time: 317.0
Solving linear variational problem.
    Residual0: 5158.0731434659865
    Residual: 1.2820002011804278e-10
Simulation time: 327.0
Solving linear variational problem.
    Residual0: 4848.794263240909
    Residual: 1.159693130235692e-10
Simulation time: 337.0
Solving linear variational problem.
    Residual0: 4568.710195417492
    Residual: 1.1805728385664729e-10
Simulation time: 347.0
Solving linear variational problem.
    Residual0: 4314.5091124375795
    Residual: 1.2584638026958384e-10
Simulation time: 357.0
Solving linear variational problem.
    Residual0: 4083.312018305163
    Residual: 9.47205327802508e-11
Simulation time: 367.0
Solving linear variational problem.
 

Simulation time: 1.0
Solving linear variational problem.
    Residual0: 512124.34511254245
    Residual: 14290.226747112582
    Residual: 54.317336244958504
    Residual: 0.00565256387118617
Simulation time: 2.0
Solving linear variational problem.
    Residual0: 208238.1516296933
    Residual: 5039.550023515934
    Residual: 13.000325251669079
    Residual: 0.00023631142196308877
Simulation time: 3.0
Solving linear variational problem.
    Residual0: 149859.78932669896
    Residual: 2260.993178092335
    Residual: 4.327117720707776
    Residual: 3.868403903313777e-05
Simulation time: 4.0
Solving linear variational problem.
    Residual0: 118331.68526599102
    Residual: 513.648588738119
    Residual: 0.23816362374308014
Simulation time: 5.0
Solving linear variational problem.
    Residual0: 98459.63416613569
    Residual: 79.13849647013055
    Residual: 0.0005208707800584594
Simulation time: 6.0
Solving linear variational problem.
    Residual0: 84759.44614903453
    Residual: 799.8942

    Residual: 8.285950019359465e-11
Simulation time: 397.0
Solving linear variational problem.
    Residual0: 1671.306439578168
    Residual: 7.357312214988403e-11
Simulation time: 407.0
Solving linear variational problem.
    Residual0: 1597.1184948329615
    Residual: 7.218914919832599e-11
Simulation time: 417.0
Solving linear variational problem.
    Residual0: 1528.8032007549048
    Residual: 8.278100024618186e-11
Simulation time: 427.0
Solving linear variational problem.
    Residual0: 1465.7598957026028
    Residual: 7.928484854311497e-11
Simulation time: 437.0
Solving linear variational problem.
    Residual0: 1407.4538634250132
    Residual: 7.771762903176933e-11
Simulation time: 447.0
Solving linear variational problem.
    Residual0: 1353.408662092402
    Residual: 7.50727760476403e-11
Simulation time: 457.0
Solving linear variational problem.
    Residual0: 1303.1994980502654
    Residual: 8.069856728056716e-11
Simulation time: 467.0
Solving linear variational problem.
    R

    Residual: 9.347488815307262e-05
Simulation time: 9.0
Solving linear variational problem.
    Residual0: 91343.17109102882
    Residual: 1936.6638842024718
    Residual: 1.7108497064352637
    Residual: 3.0569832706069163e-06
Simulation time: 10.0
Solving linear variational problem.
    Residual0: 83873.65073074304
    Residual: 35.57385448185459
    Residual: 0.00020751955397524082
Simulation time: 11.0
Solving linear variational problem.
    Residual0: 77659.22380220446
    Residual: 15.21649764910308
    Residual: 0.00012541074594632818
Simulation time: 12.0
Solving linear variational problem.
    Residual0: 72399.27711995004
    Residual: 3.2587062490447924
    Residual: 3.7471400309697704e-06
Simulation time: 13.0
Solving linear variational problem.
    Residual0: 67883.13146914142
    Residual: 394.1376286882591
    Residual: 0.07648832392736005
Simulation time: 14.0
Solving linear variational problem.
    Residual0: 63958.59905408383
    Residual: 5.072044405965958
    Residu

...

Solving linear variational problem.
    Residual: 393.7741655781649
    Residual: 9.180985606683226e-11
Simulation time: 23.0
Solving linear variational problem.
    Residual0: 20206.89807878421
    Residual: 1.3257304186342385e-10
Simulation time: 24.0
Solving linear variational problem.
    Residual0: 23447.650401443818
    Residual: 1.736753390410264e-10
Simulation time: 25.0
Solving linear variational problem.
    Residual0: 13680.589084688312
    Residual: 1.1809336566064431e-10
Simulation time: 26.0
Solving linear variational problem.
    Residual0: 10279.05332951714
    Residual: 1.0107410457551741e-10
Simulation time: 27.0
Solving linear variational problem.
    Residual0: 8191.354099172881
    Residual: 9.724287525705104e-11
Simulation time: 37.0
Solving linear variational problem.
    Residual0: 32529.433400584294
    Residual: 2.4834035539175416e-10
Simulation time: 47.0
Solving linear variational problem.
    Residual0: 16857.824407384192
    Residual: 1.5016110790762837e-1

0.9948635445075212
Simulation time: 7.0
Solving linear variational problem.
Solving linear variational problem.
0.9953878880018276
Simulation time: 8.0
Solving linear variational problem.
Solving linear variational problem.
0.9958734399292322
Simulation time: 9.0
Solving linear variational problem.
Solving linear variational problem.
0.9963274797695435
Simulation time: 10.0
Solving linear variational problem.
Solving linear variational problem.
0.9967552613137378
Simulation time: 11.0
Solving linear variational problem.
Solving linear variational problem.
0.9971607231571412
Simulation time: 12.0
Solving linear variational problem.
Solving linear variational problem.
0.9975501097023485
Simulation time: 13.0
Solving linear variational problem.
Solving linear variational problem.
0.9979284110752884
Simulation time: 14.0
Solving linear variational problem.
Solving linear variational problem.
0.9982965907533538
Simulation time: 15.0
Solving linear variational problem.
Solving linear variati

    Residual: 9.280455884157147e-11
Simulation time: 237.0
Solving linear variational problem.
    Residual0: 509.73699366500205
    Residual: 9.003142482297836e-11
Simulation time: 247.0
Solving linear variational problem.
    Residual0: 468.3025126454023
    Residual: 9.110250634449454e-11
Simulation time: 257.0
    Residual0: 431.7352747159208
Solving linear variational problem.
    Residual: 8.830756487719431e-11
Simulation time: 267.0
Solving linear variational problem.
    Residual0: 399.31636061085385
    Residual: 9.436010157994005e-11
Simulation time: 277.0
Solving linear variational problem.
    Residual0: 370.45866541819424
    Residual: 8.892113257947698e-11
Simulation time: 287.0
Solving linear variational problem.
    Residual0: 344.6781129812442
    Residual: 9.575359837118974e-11
Simulation time: 297.0
Solving linear variational problem.
    Residual0: 321.57190570749924
    Residual: 9.06156565063819e-11
Simulation time: 307.0
Solving linear variational problem.
    Re

0.993593808268398
Simulation time: 35.0
Solving linear variational problem.
Solving linear variational problem.
0.9934109332525193
Simulation time: 36.0
Solving linear variational problem.
Solving linear variational problem.
0.9932417318281217
Shakedown!
CPU times: user 1min 12s, sys: 5.59 s, total: 1min 17s
Wall time: 1min 14s


[582.03125, 582.03125, 58.59375, 58.59375]